In [2]:
import pandas as pd
from datetime import datetime
import plotly.express as px
import plotly.graph_objects as go

In [4]:
df = pd.read_csv('data\JUUL metadata_Jun24.txt', delimiter='\t') 
#print(df.head())

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\3807613224.py:1: DtypeWarning: Columns (27) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('data\JUUL metadata_Jun24.txt', delimiter='\t')


In [5]:
print(df.shape) # 1583962 records as of 6/14/2024

(1583962, 28)


In [6]:
df['assigned_topic'] = df['topic'].str.split(';').str.get(0)
df = df.drop(df[df['assigned_topic'].str.len() > 100].index) # 2 email records dropped due to wrong topic label

In [ ]:
df.columns

In [7]:
email_df = df[df['type'].str.contains('email', case=False, na=False)]
print(email_df.shape) #1106046 email records as of 6/14/2024

(1106046, 29)


In [ ]:
null_values = email_df.isnull().sum()
print(null_values)

Missing values summary for email records

* id                      0
* datesent                2
* datereceived       333992
* title                3125
* author              13143
* documentdate            0
* type                    0
* recipient           50241
* topic              863932
* copied             662273

### Time series analysis by topic - Monthly & Yearly
Where there any particular topics that stood out?



In [ ]:
email_df['documentdate'] = pd.to_datetime(email_df['documentdate'], format='mixed')
print(email_df.dtypes)

In [10]:
# Group by month and overall topic, visualize the graph - email records
email_df['month'] = email_df['documentdate'].dt.to_period('M')
monthly_topic_counts = email_df.groupby(['month', 'assigned_topic']).size().reset_index(name='document_count')

fig = go.Figure()

# Add a trace for each topic
for topic in monthly_topic_counts['assigned_topic'].unique():
    topic_data = monthly_topic_counts[monthly_topic_counts['assigned_topic'] == topic]
    fig.add_trace(go.Scatter(x=topic_data['month'].astype(str), y=topic_data['document_count'],
                             mode='lines', name=topic))

# Layout - titles
fig.update_layout(
    title='Document Counts by Month and Broad Topic',
    xaxis_title='Month',
    yaxis_title='Number of Documents',
    legend_title='Broad Topic')

fig.show()

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\523080233.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  email_df['month'] = email_df['documentdate'].dt.to_period('M')


In [11]:
# Group by month and overall topic, visualize the graph - email records
email_df['month'] = email_df['documentdate'].dt.to_period('M')
monthly_topic_counts = email_df.groupby(['month', 'assigned_topic', 'topic']).size().reset_index(name='document_count')

fig = go.Figure()

# Add a trace for each detailed topic
for topic in monthly_topic_counts['topic'].unique():
    topic_data = monthly_topic_counts[monthly_topic_counts['topic'] == topic]
    fig.add_trace(go.Scatter(x=topic_data['month'].astype(str), y=topic_data['document_count'],
                             mode='lines', name=topic))

# Get unique assigned topics for the dropdown filter
assigned_topics = monthly_topic_counts['assigned_topic'].unique()

# Create dropdown buttons
dropdown_buttons = [{'label': 'All Topics', 'method': 'update', 'args': [{'visible': [True] * len(fig.data)}, {'title': 'Document Counts by Month and Topic'}]}]

for assigned_topic in assigned_topics:
    visibility = [(trace.name in monthly_topic_counts[monthly_topic_counts['assigned_topic'] == assigned_topic]['topic'].values) for trace in fig.data]
    dropdown_buttons.append({
        'label': assigned_topic,
        'method': 'update',
        'args': [{'visible': visibility},
                 {'title': f'Document Counts by Month for {assigned_topic}'}]})

# Layout - titles and dropdown
fig.update_layout(
    title='Document Counts by Month and Topic',
    xaxis_title='Month',
    yaxis_title='Number of Documents',
    legend_title='Topic',
    updatemenus=[{'buttons': dropdown_buttons,
                  'direction': 'down',
                  'showactive': True,}])

# Show the plot
fig.show()


C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\3580354168.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [14]:
# Group by year and overall topic, visualize the graph - email records
email_df['year'] = email_df['documentdate'].dt.year
yearly_topic_counts = email_df.groupby(['year', 'assigned_topic']).size().reset_index(name='document_count')

fig = go.Figure()

# Add a trace for each topic
for topic in yearly_topic_counts['assigned_topic'].unique():
    topic_data = yearly_topic_counts[yearly_topic_counts['assigned_topic'] == topic]
    fig.add_trace(go.Scatter(x=topic_data['year'].astype(str), y=topic_data['document_count'],
                             mode='lines', name=topic))

# Layout - titles
fig.update_layout(
    title='Document Counts by Year and Broad Topic',
    xaxis_title='Year',
    yaxis_title='Number of Documents',
    legend_title='Broad Topic')

fig.show()

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\1035237355.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [15]:
# Group by year and topic, visualize the graph - email records
email_df['year'] = email_df['documentdate'].dt.year
yearly_topic_counts = email_df.groupby(['year', 'assigned_topic', 'topic']).size().reset_index(name='document_count')

fig = go.Figure()

# Add a trace for each detailed topic
for topic in yearly_topic_counts['topic'].unique():
    topic_data = yearly_topic_counts[yearly_topic_counts['topic'] == topic]
    fig.add_trace(go.Scatter(x=topic_data['year'], y=topic_data['document_count'],
                             mode='lines', name=topic))

# Get unique assigned topics for the dropdown filter
assigned_topics = yearly_topic_counts['assigned_topic'].unique()

# Create dropdown buttons
dropdown_buttons = [{'label': 'All Topics', 'method': 'update', 'args': [{'visible': [True] * len(fig.data)}, {'title': 'Document Counts by Year and Topic'}]}]

for assigned_topic in assigned_topics:
    visibility = [(trace.name in yearly_topic_counts[yearly_topic_counts['assigned_topic'] == assigned_topic]['topic'].values) for trace in fig.data]
    dropdown_buttons.append({
        'label': assigned_topic,
        'method': 'update',
        'args': [{'visible': visibility},
                 {'title': f'Document Counts by Year for {assigned_topic}'}]})

# Layout - titles and dropdown
fig.update_layout(
    title='Document Counts by Year and Topic',
    xaxis_title='Year',
    yaxis_title='Number of Documents',
    legend_title='Topic',
    updatemenus=[{'buttons': dropdown_buttons,
                  'direction': 'down',
                  'showactive': True,}])
# Show the plot
fig.show()

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\1888259318.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Time series analysis by author

In [16]:
import re
# Function to extract email addresses
def extract_email(text):
    if isinstance(text, str):
        # Regular expression to match email addresses
        email_pattern = re.compile(r'\b[A-Za-z0-9._%+-]+@[A-Za-z0-9.-]+\.[A-Z|a-z]{2,}\b')
        emails = email_pattern.findall(text)
        return emails[0] if emails else None
    return None

email_df['author_email'] = email_df['author'].apply(extract_email)

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\4160740892.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



* id                      0
* author              13143
* author_email       200101, ~18% of records with missing emails

In [ ]:
email_df[['author', 'author_email']]

In [ ]:
unique_author_emails = email_df['author_email'].unique()
unique_author_email_count = len(unique_author_emails)
print(f"Number of unique author emails: {unique_author_email_count}")


Number of unique author emails: 21202


In [17]:
# Group by year and author, visualize the graph - email records
email_df['year'] = pd.to_datetime(email_df['documentdate']).dt.year
author_total_counts = email_df.groupby('author_email').size().reset_index(name='total_count')
top_150_authors = author_total_counts.nlargest(150, 'total_count')['author_email']
filtered_email_df = email_df[email_df['author_email'].isin(top_150_authors)]
yearly_topic_counts = filtered_email_df.groupby(['year', 'author_email']).size().reset_index(name='document_count')

fig = go.Figure()

# Add a trace for each author
for author in yearly_topic_counts['author_email'].unique():
    author_data = yearly_topic_counts[yearly_topic_counts['author_email'] == author]
    fig.add_trace(go.Scatter(x=author_data['year'].astype(str), y=author_data['document_count'],
                             mode='lines', name=author, visible='legendonly'))

# Add dropdown filter
dropdown_buttons = [
    {'label': 'All Authors', 'method': 'update', 'args': [{'visible': [True]*len(fig.data)}, {'title': 'Document Counts by Year and Top 150 Authors'}]}]

for i, author in enumerate(yearly_topic_counts['author_email'].unique()):
    visible = [False]*len(fig.data)
    visible[i] = True
    dropdown_buttons.append({'label': author, 'method': 'update', 'args': [{'visible': visible}, {'title': f'Document Counts by Year for {author}'}]})

fig.update_layout(
    updatemenus=[{
        'buttons': dropdown_buttons,
        'direction': 'down',
        'showactive': True
    }],
    title='Document Counts by Year and Top 150 Authors',
    xaxis_title='Year',
    yaxis_title='Number of Documents',
    legend_title='Author')

fig.show()

C:\Users\rolando\AppData\Local\Temp\ipykernel_14244\776406042.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [18]:
# Group by year, author, and topic
yearly_topic_counts = filtered_email_df.groupby(['year', 'author_email', 'assigned_topic']).size().reset_index(name='document_count')

fig = go.Figure()

# Add traces for each author and topic
for author in yearly_topic_counts['author_email'].unique():
    author_data = yearly_topic_counts[yearly_topic_counts['author_email'] == author]
    for topic in author_data['assigned_topic'].unique():
        topic_data = author_data[author_data['assigned_topic'] == topic]
        fig.add_trace(go.Scatter(x=topic_data['year'].astype(str), y=topic_data['document_count'],
                                 mode='lines', name=f'{author} - {topic}', visible=False))

# Make the first author's traces visible by default
initial_author = yearly_topic_counts['author_email'].unique()[0]
for i, trace in enumerate(fig.data):
    if initial_author in trace.name:
        fig.data[i].visible = True

# Create dropdown menu
dropdown_buttons = []
for author in yearly_topic_counts['author_email'].unique():
    visible = [author in trace.name for trace in fig.data]
    button = dict(label=author,
                  method="update",
                  args=[{"visible": visible},
                        {"title": f"Document Counts by Year for {author}"}])
    dropdown_buttons.append(button)

# Update layout with dropdown
fig.update_layout(
    title=f'Document Counts by Year for {initial_author}',
    xaxis_title='Year',
    yaxis_title='Number of Documents',
    legend_title='Topic',
    updatemenus=[{
        "buttons": dropdown_buttons,
        "direction": "down",
        "showactive": True,}])

fig.show()

**Other Records** - Might not be worth exploring as ~50% of topic labels are missing

In [ ]:
other_records_df = df[~df['type'].str.contains('email', case=False, na=False)]
print(other_records_df.shape) #477914 other records as of 6/14/2024

(477914, 29)


In [ ]:
null_values = other_records_df.isnull().sum()
print(null_values)

Missing values summary for other records
* id                     0
* datesent          406935
* datereceived      413356
* title             145183
* author            322886
* documentdate         639
* type                3399
* topic             280654



In [ ]:
other_records_df = other_records_df.dropna(subset=['documentdate']) #drop the 639 records with missing document date

In [ ]:
df['documentdate'] = df['documentdate'].str.split(';').apply(lambda x: [d.strip() for d in x])

In [ ]:
def process_dates(dates):
    try:
        first_date = pd.to_datetime(dates[0], format='mixed')
    except ValueError:
        return None

    if first_date < datetime(2000, 1, 1) and len(dates) > 1:
        try:
            second_date = pd.to_datetime(dates[1], format='mixed')
            return second_date.strftime('%Y-%m-%d')
        except ValueError:
            return first_date.strftime('%Y-%m-%d')

    return first_date.strftime('%Y-%m-%d')

In [ ]:
df['month'] = df['processed_documentdate'].dt.to_period('M')
monthly_topic_counts = df.groupby(['month', 'topic']).size().reset_index(name='document_count')

# Print the first 100 rows of the aggregated data
print(monthly_topic_counts.head())